# Flight delays
predict whether a flight will be delayed for more than 15 mins

In [81]:
#importing libraries
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score
from xgboost import XGBClassifier
import scipy.stats as stats

In [2]:
#importing data
df_train = pd.read_csv('data/flight_delays_train.csv')
df_test = pd.read_csv('data/flight_delays_test.csv')

In [3]:
df_train.head()

Month DayofMonth DayOfWeek  DepTime UniqueCarrier Origin Dest  Distance  \
0   c-8       c-21       c-7     1934            AA    ATL  DFW       732   
1   c-4       c-20       c-3     1548            US    PIT  MCO       834   
2   c-9        c-2       c-5     1422            XE    RDU  CLE       416   
3  c-11       c-25       c-6     1015            OO    DEN  MEM       872   
4  c-10        c-7       c-6     1828            WN    MDW  OMA       423   

  dep_delayed_15min  
0                 N  
1                 N  
2                 N  
3                 N  
4                 Y

In [5]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 9 columns):
 #   Column             Non-Null Count   Dtype 
---  ------             --------------   ----- 
 0   Month              100000 non-null  object
 1   DayofMonth         100000 non-null  object
 2   DayOfWeek          100000 non-null  object
 3   DepTime            100000 non-null  int64 
 4   UniqueCarrier      100000 non-null  object
 5   Origin             100000 non-null  object
 6   Dest               100000 non-null  object
 7   Distance           100000 non-null  int64 
 8   dep_delayed_15min  100000 non-null  object
dtypes: int64(2), object(7)
memory usage: 6.9+ MB


In [45]:
#data seems to be clean but lets manipulate it for our model

df_train['hour'] = df_train['DepTime'] // 100
numerical_cols = [
    #'DepTime', removed because added hour instead
    'Distance']
categorical_cols = ['Month', 'DayofMonth', 'DayOfWeek', 'UniqueCarrier', 'Origin', 'Dest', 'hour']
dum = pd.get_dummies(df_train[categorical_cols], drop_first=True)
scaler = StandardScaler()
num = scaler.fit_transform(df_train[numerical_cols])
scaled_df = pd.DataFrame(num, columns=numerical_cols)
df_train_x = pd.concat([scaled_df, dum], axis=1)
df_train_y = df_train['dep_delayed_15min'].map({'Y': 1, 'N':0}).values



In [46]:
#divide the data
X_train, X_valid, y_train, y_valid = train_test_split(df_train_x, df_train_y, test_size=0.3)

In [66]:
#train the logistic regression
lgr = LogisticRegression(C=0.1,max_iter=1000).fit(X_train, y_train)

In [67]:
#predict
prediction = lgr.predict_proba(X_valid)[:,1]

In [68]:
#score
roc_auc_score(y_valid, prediction)

np.float64(0.7119833574475742)

### Result with scaled hour: 

np.float64(0.7086818172062379)

### Result with one hot encoded hour:

np.float64(0.7099086975943645)

In [62]:
#lets try hyperparameter tuning to get a better result
params = {
    'C': [0.001, 0.01, 0.1, 1, 10, 100],
    'penalty': ['l2'],
    'solver': ['lbfgs'], # Default solver
    'max_iter': [1000, 2000],
    'class_weight': [None, 'balanced']
}

cv = GridSearchCV(lgr, params, verbose=2)

In [63]:
cv.fit(X_train, y_train)

Fitting 5 folds for each of 24 candidates, totalling 120 fits
[CV] END C=0.001, class_weight=None, max_iter=1000, penalty=l2, solver=lbfgs; total time=   1.7s
[CV] END C=0.001, class_weight=None, max_iter=1000, penalty=l2, solver=lbfgs; total time=   1.3s
[CV] END C=0.001, class_weight=None, max_iter=1000, penalty=l2, solver=lbfgs; total time=   1.4s
[CV] END C=0.001, class_weight=None, max_iter=1000, penalty=l2, solver=lbfgs; total time=   1.2s
[CV] END C=0.001, class_weight=None, max_iter=1000, penalty=l2, solver=lbfgs; total time=   1.5s
[CV] END C=0.001, class_weight=None, max_iter=2000, penalty=l2, solver=lbfgs; total time=   1.4s
[CV] END C=0.001, class_weight=None, max_iter=2000, penalty=l2, solver=lbfgs; total time=   1.2s
[CV] END C=0.001, class_weight=None, max_iter=2000, penalty=l2, solver=lbfgs; total time=   1.3s
[CV] END C=0.001, class_weight=None, max_iter=2000, penalty=l2, solver=lbfgs; total time=   1.2s
[CV] END C=0.001, class_weight=None, max_iter=2000, penalty=l2, s

/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/sklearn/linear_model/_logistic.py:465: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. OF ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


[CV] END C=100, class_weight=balanced, max_iter=1000, penalty=l2, solver=lbfgs; total time=  24.5s
[CV] END C=100, class_weight=balanced, max_iter=1000, penalty=l2, solver=lbfgs; total time=  25.5s
[CV] END C=100, class_weight=balanced, max_iter=1000, penalty=l2, solver=lbfgs; total time=  23.3s
[CV] END C=100, class_weight=balanced, max_iter=2000, penalty=l2, solver=lbfgs; total time=  26.9s
[CV] END C=100, class_weight=balanced, max_iter=2000, penalty=l2, solver=lbfgs; total time=  21.7s
[CV] END C=100, class_weight=balanced, max_iter=2000, penalty=l2, solver=lbfgs; total time=  25.7s
[CV] END C=100, class_weight=balanced, max_iter=2000, penalty=l2, solver=lbfgs; total time=  29.1s
[CV] END C=100, class_weight=balanced, max_iter=2000, penalty=l2, solver=lbfgs; total time=  30.7s


GridSearchCV(estimator=LogisticRegression(max_iter=1000),
             param_grid={'C': [0.001, 0.01, 0.1, 1, 10, 100],
                         'class_weight': [None, 'balanced'],
                         'max_iter': [1000, 2000], 'penalty': ['l2'],
                         'solver': ['lbfgs']},
             verbose=2)

In [73]:
cv_predict = cv.predict_proba(X_valid)[:,1]
roc_auc_score(y_valid, cv_predict)

np.float64(0.7119833574475742)

In [75]:
#lets use xgbclassifier
xgbc = XGBClassifier(use_label_encoder=False,eval_metric='auc', n_estimators=100)
xgbc.fit(X_train,y_train)

/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [19:22:08] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)


XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric='auc', feature_types=None,
              feature_weights=None, gamma=None, grow_policy=None,
              importance_type=None, interaction_constraints=None,
              learning_rate=None, max_bin=None, max_cat_threshold=None,
              max_cat_to_onehot=None, max_delta_step=None, max_depth=None,
              max_leaves=None, min_child_weight=None, missing=nan,
              monotone_constraints=None, multi_strategy=None, n_estimators=100,
              n_jobs=None, num_parallel_tree=None, ...)

In [76]:
xgbc_predict = xgbc.predict_proba(X_valid)[:,1]

In [77]:
roc_auc_score(y_valid, xgbc_predict)

np.float64(0.7397744334687125)

Best score so far

In [79]:
#to make sure that us changing DepTime didnt change anythin
numerical_cols = ['DepTime','Distance']
categorical_cols = ['Month', 'DayofMonth', 'DayOfWeek', 'UniqueCarrier', 'Origin', 'Dest']
dum = pd.get_dummies(df_train[categorical_cols], drop_first=True)
scaler = StandardScaler()
num = scaler.fit_transform(df_train[numerical_cols])
scaled_df = pd.DataFrame(num, columns=numerical_cols)
df_train_x = pd.concat([scaled_df, dum], axis=1)
df_train_y = df_train['dep_delayed_15min'].map({'Y': 1, 'N':0}).values

xgbc_date_changed = XGBClassifier(use_label_encoder=False,eval_metric='auc', n_estimators=100)
xgbc_date_changed.fit(X_train,y_train)
xgbc_predict_date_changed = xgbc_date_changed.predict_proba(X_valid)[:,1]
roc_auc_score(y_valid, xgbc_predict_date_changed)

/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [19:27:20] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)


np.float64(0.7397744334687125)

Nope it didnt change anything.

In [87]:
#now lets use hyperparameter tuning for the xgboost
param_xgbc = {
    # n_estimators: Number of gradient boosted trees. Equivalent to number of boosting rounds.
    'n_estimators': [100, 200, 300],  # Start with a few options

    # learning_rate (eta): Step size shrinkage used in update to prevents overfitting.
    # After each boosting step, we can directly get the weights of new features,
    # and eta shrinks the feature weights to make the boosting process more conservative.
    'learning_rate': [0.01, 0.05, 0.1],

    # max_depth: Maximum depth of a tree. Increasing this value will make the model
    # more complex and more likely to overfit.
    'max_depth': [3, 4, 5, 6], # Common range

    # min_child_weight: Minimum sum of instance weight (hessian) needed in a child.
    # If the tree partition step results in a leaf node with the sum of instance weight
    # less than min_child_weight, then the building process will give up further partitioning.
    # In linear regression task, this simply corresponds to minimum number of instances needed
    # to be in each node. The larger min_child_weight is, the more conservative the algorithm will be.
    'min_child_weight': [1, 3, 5],

    # gamma (min_split_loss): Minimum loss reduction required to make a further partition on a leaf node of the tree.
    # The larger gamma is, the more conservative the algorithm will be.
    'gamma': [0.0, 0.1, 0.2],

    # subsample: Subsample ratio of the training instances. Setting it to 0.5 means that
    # XGBoost would randomly sample half of the training data prior to growing trees.
    # and this will prevent overfitting. Subsampling will occur once in every boosting iteration.
    'subsample': [0.7, 0.8, 0.9],

    # colsample_bytree: Subsample ratio of columns when constructing each tree.
    # Subsampling occurs once for every tree constructed.
    'colsample_bytree': [0.7, 0.8, 0.9],

    # reg_alpha (L1 regularization term on weights): Increasing this value will make model more conservative.
    'reg_alpha': [0, 0.001, 0.01, 0.1],

    # reg_lambda (L2 regularization term on weights): Increasing this value will make model more conservative.
    'reg_lambda': [0.1, 1, 10],

    # scale_pos_weight: Control the balance of positive and negative weights, useful for unbalanced classes.
    # A typical value to consider: sum(negative instances) / sum(positive instances)
    # If your classes are imbalanced, calculate this value from your y_train and include it.
    # For example:
    # from collections import Counter
    # counter = Counter(y_train) # Assuming y_train is your training labels
    # scale_pos_weight_val = counter[0] / counter[1] # For binary 0/1 labels
    # 'scale_pos_weight': [1, scale_pos_weight_val] # Then include it in the grid
    # If you are not sure or classes are balanced, you can omit it or set it to [1]
    'scale_pos_weight': [1] # Default, assuming balanced or handled elsewhere for now
}

xgbc_cv = GridSearchCV(xgbc_date_changed, param_xgbc, verbose=2, scoring='roc_auc', n_jobs=-1)

In [88]:
xgbc_cv.fit(X_train, y_train)

Fitting 5 folds for each of 34992 candidates, totalling 174960 fits


/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [19:36:30] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)
/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [19:36:30] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)
/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [19:36:30] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)
/Users/bahacelik/Library/Caches/pypoetry/virtualenvs

[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0, reg_lambda=0.1, scale_pos_weight=1, subsample=0.7; total time=   8.5s
[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0, reg_lambda=0.1, scale_pos_weight=1, subsample=0.8; total time=   8.7s
[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0, reg_lambda=0.1, scale_pos_weight=1, subsample=0.8; total time=   8.7s
[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0, reg_lambda=0.1, scale_pos_weight=1, subsample=0.7; total time=   8.7s
[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0, reg_lambda=0.1, scale_pos_weight=1, subsample=0.7; total time=   8.8s
[CV] END colsample_b

/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [19:36:38] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)
/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [19:36:38] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)
/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [19:36:38] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)
/Users/bahacelik/Library/Caches/pypoetry/virtualenvs

[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0, reg_lambda=0.1, scale_pos_weight=1, subsample=0.8; total time=   7.8s
[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0, reg_lambda=0.1, scale_pos_weight=1, subsample=0.9; total time=   7.7s
[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0, reg_lambda=0.1, scale_pos_weight=1, subsample=0.8; total time=   8.2s
[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0, reg_lambda=0.1, scale_pos_weight=1, subsample=0.9; total time=   7.9s
[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0, reg_lambda=0.1, scale_pos_weight=1, subsample=0.9; total time=   7.9s
[CV] END colsample_b

...

/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [15:56:20] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)
/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [15:56:21] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)


[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.05, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0.01, reg_lambda=0.1, scale_pos_weight=1, subsample=0.8; total time=   9.5s


/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [15:56:23] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)
/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [15:56:23] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)
/Users/bahacelik/Library/Caches/pypoetry/virtualenvs/mlcourse-J5ZHcbuN-py3.11/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [15:56:23] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)
/Users/bahacelik/Library/Caches/pypoetry/virtualenvs

[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.05, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0.01, reg_lambda=0.1, scale_pos_weight=1, subsample=0.8; total time=   9.4s
[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.05, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0.01, reg_lambda=0.1, scale_pos_weight=1, subsample=0.8; total time=   8.9s
[CV] END colsample_bytree=0.7, gamma=0.0, learning_rate=0.05, max_depth=3, min_child_weight=1, n_estimators=100, reg_alpha=0.01, reg_lambda=0.1, scale_pos_weight=1, subsample=0.8; total time=   8.8s


KeyboardInterrupt: 